In [1]:
from __future__ import print_function  # needed for Python 2
from __future__ import division        # needed for Python 2
import csv # csv reader
import re # regular expressions

#import nltk # Need to download the following to add to the Python environment
#nltk.download('stopwords')
#nltk.download('wordnet')

import string
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.svm import LinearSVC
from nltk.classify import SklearnClassifier
from random import shuffle
from sklearn.pipeline import Pipeline
from sklearn.metrics import precision_recall_fscore_support, accuracy_score

from collections import Counter

In [2]:
# load data from a file and append it to rawData
def loadData(path, Text=None):
    with open(path) as f:
        header = f.readline() # Skip header line of file containing column names
        reader = csv.reader(f, delimiter='\t')
        for line in reader:
            
            # Original version of code only including Id, review text and spam (real or fake) label
            '''(Id, Text, Label) = parseReview(line)
            rawData.append((Id, Text, Label))
            preprocessedData.append((Id, preProcess(Text), Label))'''
            
            # Revised version of code adding review rating, verified purchase and product ID
            (Id, Text, Label, Rating, Verified, ProductID) = parseReview(line)
            rawData.append((Id, Text, Label, Rating, Verified, ProductID))
            preprocessedData.append((Id, preProcess(Text), Label, Rating, Verified, ProductID))
            
    f.close()
        
# split data into training and test sets
def splitData(percentage): 
    dataSamples = len(rawData)
    halfOfData = int(len(rawData)/2)
    trainingSamples = int((percentage*dataSamples)/2)
    
    # Original version of code only including Id, review text and spam real or fake label
    '''for (_, Text, Label) in rawData[:trainingSamples] + rawData[halfOfData:halfOfData+trainingSamples]:
        trainData.append((toFeatureVector(preProcess(Text)),Label))
        
        # Add features from training data (not including test data) to featureDict
        for token in toFeatureVector(preProcess(Text)):
            if token in featureDict:
                featureDict[token] += 1
            else:
                featureDict[token] = 1
                
    for (_, Text, Label) in rawData[trainingSamples:halfOfData] + rawData[halfOfData+trainingSamples:]:
        testData.append((toFeatureVector(preProcess(Text)),Label))'''
    
    # Revised version of code adding review rating, verified purchase and product ID
    for (_, Text, Label, Rating, Verified, ProductID) in rawData[:trainingSamples] + rawData[halfOfData:halfOfData+trainingSamples]:
        trainData.append((toFeatureVector(preProcess(Text), Rating, Verified, ProductID), Label))
        
        # Add features from training data (not including test data) to featureDict
        for token in toFeatureVector(preProcess(Text), Rating, Verified, ProductID):
            if token in featureDict:
                featureDict[token] += 1
            else:
                featureDict[token] = 1
    
    for (_, Text, Label, Rating, Verified, ProductID) in rawData[trainingSamples:halfOfData] + rawData[halfOfData+trainingSamples:]:
        testData.append((toFeatureVector(preProcess(Text), Rating, Verified, ProductID), Label))
        

In [3]:
# QUESTION 1

# Convert line information from input file into a tuple
def parseReview(reviewLine):
    
    # Variables to hold an integer ID, a string containing the review, and a string indicating the label
    lineID = reviewLine[0]
    lineText = reviewLine[8]
    lineLabel = 'real'
    if reviewLine[1] == '__label1__':
        lineLabel = 'fake'
    
    # Revised version also returns rating, verified purchase and product ID
    lineRating = reviewLine[2]
    lineVerified = reviewLine[3]
    lineProductID = reviewLine[5]
    
    # Original version of code only including Id, review text and spam real or fake label 
    '''return (lineID, lineText, lineLabel)'''
    
    # Revised version also returns rating, verified purchase and product ID
    return (lineID, lineText, lineLabel, lineRating, lineVerified, lineProductID)


In [4]:
# TEXT PREPROCESSING AND FEATURE VECTORIZATION

# Unigram version inputs a string of one review text to return a list of pre-processed tokens
'''def preProcess(text):
    
    # Initialise lemmatisation
    lemmatizer = WordNetLemmatizer()
    
    # Remove html tags
    tags = re.compile('<.*?>')
    text = re.sub(tags,' ', text)
    
    # split into words on whitespace
    tokens = text.split()
    
    # convert to lower case
    tokens = [word.lower() for word in tokens]
    
    # remove punctuation from each word
    tokens = [word.translate(None, string.punctuation) for word in tokens]
    
    # remove remaining tokens that are not alphabet characters (a-z)
    tokens = [word for word in tokens if word.isalpha()]
    
    # filter out stop words using nltk stopwords list
    stop_words = set(stopwords.words('english'))
    filtered_tokens = [word for word in tokens if not word in stop_words]
    
    # Apply lemmatisation
    filtered_tokens = [str(lemmatizer.lemmatize(word)) for word in filtered_tokens]
    
    return filtered_tokens'''

# Bigram version of preprocessing where no longer remove any words and add <s> and </s> tokens
def preProcess(text):
    
    # Initialise lemmatisation
    lemmatizer = WordNetLemmatizer()
    
    # Remove html tags
    tags = re.compile('<.*?>')
    text = re.sub(tags,' ', text)
    
    # Add <s> and </s> tags
    text = '<s> ' + text + ' </s>'
    text = re.sub('\.', ' </s> <s>', text)
    text = re.sub('</s> <s> </s>', '</s>', text)
    
    # split into words on whitespace
    tokens = text.split()
    
    # convert to lower case
    tokens = [word.lower() for word in tokens]
    
    # remove punctuation from each word leaving <s> and </s> tokens intact
    tokens = [word.translate(None, '\!\"\#\$\%\&\'\(\)\*\+\,\-\.\:\;\=\?\@\[\\\]\^\_\`\{\|\}\~') for word in tokens]
    
    # remove remaining tokens that are not alphabet characters (a-z) excluding <s> and </s>
    tokens = [word for word in tokens if word.isalpha() or word == '<s>' or word == '</s>']
    
    # Apply lemmatisation
    filtered_tokens = [str(lemmatizer.lemmatize(word)) for word in tokens]
    
    return filtered_tokens

In [5]:
# QUESTION 2 - Create a feature vector list of each pre-processed review to use for training the SVM

#featureDict = Counter() # A global dictionary counter of features

# Original version of code only using review text tokens as features not including duplicate tokens
'''def toFeatureVector(tokens):

    # Returns a dictionary containing features as keys, and weights as values
    
    #features = {token:1 for token in tokens} # Dictionary of features in each review without duplicates
    features = dict(Counter(tokens)) # Dictionary of features in each review including duplicates
    
    return features'''

# Revised version of code only using bigrams as features from each review text
'''def toFeatureVector(tokens):

    features = {}
    for i in range(1, len(tokens)):
        context = tokens[i-1] # Context word
        target = tokens[i] # Target word
        ngram = context + " " + target # bigram
        features[ngram] = 1
        
    return features'''

# Revised version also includes rating, whether review verified and product ID as features
'''def toFeatureVector(tokens, rating, verified, productID):
  
    # Tokens with value as number of occurrences
    features = dict(Counter(tokens))
    
    # Rating
    features['Rating'] = int(rating)
    
    # Verified
    if verified == 'Y':
        features['Verified'] = 5
    else:
        features['Verified'] = 0
    
    # Product ID
    features[productID] = 1
    
    return features'''

# Revised version using bigrams as well as rating, whether review verified and product ID
def toFeatureVector(tokens, rating, verified, productID):
    
    # Bigram features
    features = {}
    for i in range(1, len(tokens)):
        context = tokens[i-1] # Context word
        target = tokens[i] # Target word
        ngram = context + " " + target # bigram
        features[ngram] = 1
        
    # Rating
    features['Rating'] = int(rating)
    
    # Verified
    if verified == 'Y':
        features['Verified'] = 5
    else:
        features['Verified'] = 0
    
    # Product ID
    features[productID] = 1
    
    return features

In [6]:
# TRAINING AND VALIDATING OUR CLASSIFIER

def trainClassifier(trainData):
    
    print("Training Classifier...")
    
    # adjust the cost parameter and the relative weights of the two classes
    #pipeline =  Pipeline([('svc', LinearSVC())])
    pipeline =  Pipeline([('svc', LinearSVC(C = 0.05, class_weight = {0:0.45, 1:0.55}))])
    
    # Trains with Feature Dictionary as trainData[0] and Labels as trainData[1] i.e. train(train_data, train_labels) 
    return SklearnClassifier(pipeline).train(trainData)

In [7]:
# QUESTION 3

def crossValidate(dataset, folds):
    
    shuffle(dataset) # So different set of folds each time run
    cv_results = [] # List to hold final values
    sum_results = [0, 0, 0, 0] # List to hold sum total of values for all 10 folds
    foldSize = int(len(dataset)/folds) # foldsize
    
    for i in range(0,len(dataset),foldSize): # will run 10 times for 10-folds
        
        testFold = dataset[i:i + foldSize] # One fold set aside to predict labels and test scores
        trainingFolds = dataset[0:i] + dataset[i + foldSize:] # Rest of the data used for training
        classifier = trainClassifier(trainingFolds) # Apply classifier to trainingData
        y_pred = predictLabels(testFold, classifier) # Predicted labels by classifier
        y_true = list(map(lambda t: t[1], testFold)) # Correct labels of testFold
        
        # Do a binary classification calculting F1 score with beta == 1 balance between precision and recall
        # Results weighted by number of samples of each class label
        fold_results = list(precision_recall_fscore_support(y_true, y_pred, average='weighted'))
        fold_results[3] = accuracy_score(y_true, y_pred) * 100 # Add accuracy score to results for the fold
        
        sum_results = [sum(x) for x in zip(fold_results, sum_results)] # Sum fold totals for precision, recall, fscore, accuracy
     
    cv_results = [y/folds for y in sum_results] # Calculate averages over all 10 folds
    
    return cv_results

In [8]:
# PREDICTING LABELS GIVEN A CLASSIFIER - Uses feature vectors created from each review text

def predictLabels(reviewSamples, classifier):
    return classifier.classify_many(map(lambda t: t[0], reviewSamples))

def predictLabel(reviewSample, classifier):
    return classifier.classify(reviewSample[0])

In [9]:
# MAIN - Split data into training and test sets, preprocess reviews, create feature vectors, run classifier and calculate scores

# load in review data
rawData = []          # the filtered data from the dataset file (should be 21000 samples)
preprocessedData = [] # the preprocessed reviews (just to see how your preprocessing is doing)
trainData = []        # the training data as a percentage of the total dataset (currently 80%, or 16800 samples)
testData = [] # the test data as a percentage of the total dataset (currently 20%, or 4200 samples)

featureDict = Counter() # a global dictionary counter of features
most_tokens = Counter()

# the output classes
fakeLabel = 'fake'
realLabel = 'real'

# path to the data file
reviewPath = 'amazon_reviews.txt'

# parse the dataset and put it in a raw data list
print("Now %d rawData, %d trainData, %d testData" % (len(rawData), len(trainData), len(testData)),
      "Preparing the dataset...",sep='\n')

loadData(reviewPath) 

# split the raw dataset into a set of training data and a set of test data (80/20)
print("Now %d rawData, %d trainData, %d testData" % (len(rawData), len(trainData), len(testData)),
      "Preparing training and test data...",sep='\n')

splitData(0.8)

# print the number of training samples and the number of features
print("Now %d rawData, %d trainData, %d testData" % (len(rawData), len(trainData), len(testData)),
      "Training Samples: ", len(trainData), "Features: ", len(featureDict), sep='\n')

# Limit feature list to the 35000 most common features
'''print("Limiting features to the 35000 most common")
most_tokens = map(lambda t: t[0], featureDict.most_common(35000))
trainData = [({k:v for (k,v) in line[0].items() if k in most_tokens}, line[1]) for line in trainData]
testData = [({k:v for (k,v) in line[0].items() if k in most_tokens}, line[1]) for line in testData]'''

# Perform 10-fold cross validation on the 80% training data
cvResults = crossValidate(trainData, 10) 
print("\n10-fold Cross Validation average scores\nPrecision:", cvResults[0], "\nRecall:", cvResults[1], "\nF1 score:", cvResults[2], "\nAccuracy:", cvResults[3])

# Apply classifier to unseen 20% testData after training on whole 80% training set
trained_classifier = trainClassifier(trainData)
y_pred = predictLabels(testData, trained_classifier)
y_true = list(map(lambda t: t[1], testData)) # Correct labels of testFold

# testData scores
test_results = list(precision_recall_fscore_support(y_true, y_pred, average='weighted'))
test_results[3] = accuracy_score(y_true, y_pred) * 100 # Add accuracy score to results for the fold

print("\nTest Data scores\nPrecision:", test_results[0], "\nRecall:", test_results[1], "\nF1 score:", test_results[2], "\nAccuracy:", test_results[3])

Now 0 rawData, 0 trainData, 0 testData
Preparing the dataset...
Now 21000 rawData, 0 trainData, 0 testData
Preparing training and test data...
Now 21000 rawData, 16800 trainData, 4200 testData
Training Samples: 
16800
Features: 
334675
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...
Training Classifier...

10-fold Cross Validation average scores
Precision: 0.8086047874661343 
Recall: 0.8061309523809523 
F1 score: 0.8057770936369526 
Accuracy: 80.61309523809526
Training Classifier...

Test Data scores
Precision: 0.8176868886840201 
Recall: 0.8138095238095238 
F1 score: 0.8132396718877373 
Accuracy: 81.38095238095238


In [ ]:
# Summary of results varying the above classifier as described

'''
1. Only parse (Id, Text, Label) from each review.

Pre-process review text by:
Removing html tags
Splitting words on whitespace.
Removing punctuation from each word
Removing words that are not alphabet characters

Create feature vector with weights 1 for each word present not counting duplicates.

Train classifier with cost parameter C = 1.0 and equal class weighting.

Number of features: 34468

10-fold Cross Validation average scores
Precision: 0.5984150928557627 
Recall: 0.5977976190476191 
F1 score: 0.5976250300278887 
Accuracy: 59.779761904761905

Test Data scores
Precision: 0.5847619816435208 
Recall: 0.5847619047619048 
F1 score: 0.5847618106035851 
Accuracy: 58.47619047619048


2. As 1. but filter out stop words during pre-processing and apply lemmatisation

Number of features: 30527

10-fold Cross Validation average scores
Precision: 0.5933707936150516 
Recall: 0.5927976190476191 
F1 score: 0.5926363781165793 
Accuracy: 59.279761904761905

Test Data scores
Precision: 0.5642862390713395 
Recall: 0.5642857142857143 
F1 score: 0.5642848250710716 
Accuracy: 56.42857142857143


3. As 2. but try different values of cost parameter and class weightings for the SVM.
Final values C = 0.05, class weights = {0:0.45, 1:0.55}

Number of features: 30527

10-fold Cross Validation average scores
Precision: 0.6326390943073809 
Recall: 0.6310714285714286 
F1 score: 0.6301740286534767 
Accuracy: 63.107142857142854

Test Data scores
Precision: 0.5963991872049437 
Recall: 0.595 
F1 score: 0.5935250535801935 
Accuracy: 59.5


4. As 3. but adjust feature weights to include multiple occurrences of the same token in a review.

Number of features: 30527

10-fold Cross Validation average scores
Precision: 0.6285109393486832 
Recall: 0.627202380952381 
F1 score: 0.6264198998728571 
Accuracy: 62.72023809523811

Test Data scores
Precision: 0.595685543888782 
Recall: 0.5942857142857143 
F1 score: 0.5927964202863489 
Accuracy: 59.42857142857143


5. As 4. but using bigram features from the processed review text instead of unigrams and pre-processing text so
no words removed and <s> and </s> tags added.

Number of features: 319301

10-fold Cross Validation average scores
Precision: 0.6364644823695467 
Recall: 0.6358333333333334 
F1 score: 0.6355588804092513 
Accuracy: 63.58333333333333

Test Data scores
Precision: 0.6079260372360747 
Recall: 0.6076190476190476 
F1 score: 0.6073398226040104 
Accuracy: 60.76190476190476


6. As 4. (unigrams) but additionally parsing (Rating, Verified, ProductID) from each review and including them as features

Number of features: 45901

10-fold Cross Validation average scores
Precision: 0.8113612092135462 
Recall: 0.8079166666666666 
F1 score: 0.8073951985232538 
Accuracy: 80.79166666666666

Test Data scores
Precision: 0.8091666666666667 
Recall: 0.8028571428571428 
F1 score: 0.8018461538461539 
Accuracy: 80.28571428571428


7. As 6. (unigrams) but limiting the number of features to the 35000 most common.

Number of features: 35000

10-fold Cross Validation average scores
Precision: 0.8097124625600886 
Recall: 0.805952380952381 
F1 score: 0.8054196105836514 
Accuracy: 80.5952380952381

Test Data scores
Precision: 0.8079086950675126 
Recall: 0.8016666666666666 
F1 score: 0.8006563764575785 
Accuracy: 80.16666666666666


8. As 6. parsing (Rating, Verified, ProductID) as features but including bigram features instead of unigrams.

Number of features: 334675

10-fold Cross Validation average scores
Precision: 0.8064564776175909 
Recall: 0.8040476190476191 
F1 score: 0.8037342118560243 
Accuracy: 80.40476190476191

Test Data scores
Precision: 0.8176868886840201 
Recall: 0.8138095238095238 
F1 score: 0.8132396718877373 
Accuracy: 81.38095238095238

'''

In [182]:
# Code to check features
'''with open('amazon_reviews.txt') as f:
        reader = csv.reader(f, delimiter='\t')
        next(reader, None)
        for line in reader:
            (Id, Text, Label, Rating, Verified, ProductID) = parseReview(line)
            #print(preProcess(Text))
            print(toFeatureVector(preProcess(Text), Rating, Verified, ProductID))'''

{'in case': 1, 'for something': 1, '</s> <s>': 1, 'so this': 1, 'Verified': 0, 'you need': 1, 'it around': 1, 'think so': 1, 'you think': 1, 'need it': 1, 'keep it': 1, 'it for': 1, 'just keep': 1, 'product will': 1, 'this product': 1, 'will save': 1, 'case you': 1, 'B00008NG7N': 1, '<s> just': 1, 'around just': 1, 'day </s>': 1, 'least you': 1, 'Rating': 4, 'when least': 1, 'something </s>': 1, '<s> when': 1, 'save the': 1, 'the day': 1, 'just in': 1}
{'is relatively': 1, 'work at': 1, 'and provides': 1, 'Verified': 5, 'quality and': 1, 'new introduced': 1, 'their particular': 1, '</s> <s>': 1, 'battery are': 1, 'every voltage': 1, '<s> there': 1, 'keep my': 1, 'sensor in': 1, 'technical assistant': 1, 'high voltage': 1, 'at every': 1, 'but stallion': 1, 'particular </s>': 1, 'cost </s>': 1, 'a sensor': 1, 'cost is': 1, 'developing cost': 1, 'doesnt compromise': 1, 'assistant that': 1, 'built technical': 1, 'provides u': 1, 'best at': 1, 'act like': 1, 'up and': 1, 'with the': 1, 'vol

{'lost pound': 1, 'and had': 1, 'to comprehend': 1, 'even if': 1, 'short of': 1, 'only the': 1, 'review i': 1, 'for you': 1, 'for week': 1, 'active during': 1, 'to find': 1, 'regularly i': 1, '<s> although': 1, 'struggled for': 1, 'that work': 1, 'weight take': 1, 'with a': 1, 'proof that': 1, 'than pound': 1, 'kind of': 1, 'read </s>': 1, 'to try': 1, 'you im': 1, 'do that': 1, 'at my': 1, 'all </s>': 1, 'had high': 1, 'it a': 1, 'of product': 1, 'have never': 1, 'i didnt': 1, 'a few': 1, 'the use': 1, 'a product': 1, 'using it': 1, 'product but': 1, 'pound at': 1, 'in the': 1, 'pound in': 1, 'time during': 1, 'people keep': 1, 'Rating': 1, 'actually lose': 1, 'any time': 1, 'lose weight': 1, 'at least': 1, 'try something': 1, 'the product': 1, 'been nothing': 1, 'i struggled': 1, 'normally people': 1, 'at any': 1, 'wa hard': 1, 'this with': 1, 'so long': 1, 'new </s>': 1, 'of this': 1, 'wa very': 1, 'product that': 1, 'i could': 1, 'this because': 1, 'with the': 1, 'how it': 1, 'and 

{'by the': 1, 'product that': 1, 'a long': 1, 'time i': 1, 'long time': 1, 'for a': 1, '</s> <s>': 1, 'work </s>': 1, 'this mug': 1, '<s> i': 1, 'time </s>': 1, 'a much': 1, 'is the': 1, 'Verified': 0, 'thought i': 1, 'coffee in': 1, 'wellmade product': 1, '<s> overall': 1, 'mug is': 1, 'lukewarm by': 1, 'enjoy for': 1, 'i never': 1, 'overall a': 1, 'mug </s>': 1, 'be lukewarm': 1, '<s> this': 1, 'having it': 1, 'making coffee': 1, 'but i': 1, 'ever pay': 1, 'would ever': 1, 'i would': 1, 'got tired': 1, 'to enjoy': 1, 'i hope': 1, 'solution </s>': 1, 'B002PY7AYS': 1, 'never thought': 1, 'the time': 1, 'travel mug': 1, 'morning and': 1, '<s> but': 1, 'the morning': 1, 'that i': 1, 'i got': 1, 'a travel': 1, 'perfect solution': 1, 'in the': 1, 'of making': 1, 'the perfect': 1, 'Rating': 4, 'to work': 1, 'a for': 1, 'much a': 1, 'really got': 1, 'a wellmade': 1, 'it be': 1, 'and having': 1, 'hope to': 1, 'got to': 1, 'pay a': 1, 'tired of': 1, 'i really': 1}
{'backup a': 1, 'Verified': 0

{'wa not': 1, 'Verified': 0, 'or behaved': 1, 'i could': 1, 'and the': 1, '</s> <s>': 1, 'this product': 1, 'faith and': 1, '<s> i': 1, 'the local': 1, 'took a': 1, 'leap of': 1, 'nothing more': 1, 'could ask': 1, 'not available': 1, 'bought it': 1, 'of faith': 1, 'this for': 1, 'B00CW8YACW': 1, 'anywhere in': 1, 'mom and': 1, 'ask out': 1, '<s> this': 1, 'local store': 1, 'great </s>': 1, 'out of': 1, 'and bought': 1, 'a leap': 1, 'product wa': 1, 'it and': 1, 'sounded or': 1, 'it sounded': 1, 'how it': 1, 'i bought': 1, 'see how': 1, 'in the': 1, 'and nothing': 1, 'more i': 1, 'Rating': 4, '<s> hence': 1, 'to see': 1, 'is great': 1, 'the product': 1, 'behaved </s>': 1, 'hence took': 1, 'store to': 1, 'available anywhere': 1, 'my mom': 1, 'for my': 1, 'bought this': 1, 'this </s>': 1, 'of this': 1, 'product is': 1}
{'solely responsible': 1, 'i broke': 1, 'good waffle': 1, 'last one': 1, 'is not': 1, 'really have': 1, 'for a': 1, '</s> <s>': 1, 'is just': 1, '<s> i': 1, 'the thing': 1,

{'download the': 1, 'bother buying': 1, 'i wanted': 1, 'and the': 1, 'so no': 1, 'silhouette version': 1, 'every minute': 1, 'for no': 1, 'because youll': 1, 'the problem': 1, 'center doesnt': 1, 'that cannot': 1, 'it come': 1, 'repaired </s>': 1, 'up with': 1, 'got the': 1, 'come with': 1, '<s> dont': 1, 'far more': 1, 'the package': 1, 'this machine': 1, 'one could': 1, 'battery that': 1, 'i got': 1, 'no one': 1, 'Rating': 1, 'that last': 1, 'end up': 1, 'had any': 1, 'software but': 1, 'a refund': 1, 'installing it': 1, 'which wa': 1, '</s> cutting': 1, 'wa not': 1, 'youll end': 1, 'internet update': 1, 'reason </s>': 1, 'this item': 1, '<s> once': 1, 'buying this': 1, 'dont bother': 1, 'the silhouette': 1, 'wa that': 1, 'any problem': 1, 'after i': 1, 'item to': 1, 'better than': 1, 'no apparent': 1, 'bought cricut': 1, 'with battery': 1, 'machine because': 1, 'the fact': 1, 'cricut explore': 1, 'to install': 1, 'beat silhouette': 1, 'wa far': 1, 'something that': 1, 'worst thing':

...

{'cam for': 1, 'this package': 1, 'incredible how': 1, 'is amazing': 1, 'of security': 1, 'this kind': 1, 'really impressive': 1, 'kind of': 1, 'smartphone thanks': 1, 'B00TZWE140': 1, 'impressive and': 1, 'one clothes': 1, 'my girlfriend': 1, 'he recently': 1, 'in the': 1, 'Rating': 5, 'each security': 1, 'install in': 1, 'came here': 1, 'recently he': 1, 'own of': 1, 'camera on': 1, 'of these': 1, 'security camera': 1, 'code scan': 1, 'the quality': 1, 'android smartphone': 1, 'qr code': 1, 'of device': 1, 'and is': 1, 'is incredible': 1, 'friend of': 1, 'of mine': 1, 'the distance': 1, 'place </s>': 1, 'can watch': 1, 'of one': 1, 'he came': 1, 'thanks for': 1, 'security i': 1, 'and show': 1, 'a friend': 1, 'Verified': 0, 'distance he': 1, 'to bought': 1, '</s> <s>': 1, 'device security': 1, 'now im': 1, 'i took': 1, 'on his': 1, 'going to': 1, 'he can': 1, 'and now': 1, 'recently bought': 1, 'how in': 1, 'is own': 1, 'amazing a': 1, 'quality of': 1, 'took really': 1, 'bought and': 

{'con my': 1, 'not disappoint': 1, 'with all': 1, 'and one': 1, 'and i': 1, 'both with': 1, 'phone first': 1, 'two bar': 1, 'best ive': 1, 'music but': 1, 'up with': 1, 'back nothing': 1, 'becomes a': 1, 'sennheisers or': 1, 'at volume': 1, 'so it': 1, 'device a': 1, 'in mono': 1, 'your favorite': 1, 'level in': 1, 'sennheisers </s>': 1, 'are at': 1, 'purchase and': 1, 'over the': 1, 'soreness over': 1, '<s> although': 1, 'a pair': 1, 'it and': 1, 'this headphone': 1, 'well for': 1, 'to two': 1, 'looking for': 1, 'song </s>': 1, 'con with': 1, 'wa in': 1, 'sitting around': 1, 'well a': 1, 'voice from': 1, 'everyday </s>': 1, 'but i': 1, 'to these': 1, 'slip from': 1, 'return the': 1, 'headphone is': 1, '<s> volume': 1, 'caused a': 1, 'headphone if': 1, 'once pairing': 1, 'when i': 1, 'this terminology': 1, 'occurs only': 1, 'ear </s>': 1, 'work well': 1, 'dre phone': 1, 'mode people': 1, 'checked out': 1, 'at two': 1, 'also show': 1, 'if they': 1, 'fit well': 1, 'product </s>': 1, 'fit

{'Verified': 0, 'happy with': 1, 'with the': 1, 'and quality': 1, 'work </s>': 1, '<s> i': 1, 'finish my': 1, 'so happy': 1, 'expect which': 1, 'B000NIK9S2': 1, 'nice and': 1, 'reach to': 1, 'dated expect': 1, 'quality product': 1, 'to me': 1, 'to finish': 1, 'item reach': 1, 'product also': 1, '</s> <s>': 1, 'the purchase': 1, 'helped me': 1, 'purchase </s>': 1, 'also item': 1, 'my work': 1, 'me to': 1, 'me on': 1, 'which helped': 1, 'Rating': 5, 'on dated': 1, 'am so': 1, '<s> nice': 1, 'i am': 1}
{'fresh air': 1, 'Verified': 0, '</s> <s>': 1, 'perfume </s>': 1, 'really like': 1, 'the air': 1, '<s> i': 1, 'to breath': 1, 'this one': 1, 'one really': 1, 'breath </s>': 1, '<s> this': 1, 'keep the': 1, 'B00MLW6JE6': 1, 'cant do': 1, 'this just': 1, 'work to': 1, 'just keep': 1, 'the stinky': 1, 'to it': 1, 'and simple': 1, 'this purifier': 1, 'car perfume': 1, 'fresh and': 1, 'it seems': 1, 'air fresh': 1, 'i cant': 1, 'simple to': 1, 'stinky car': 1, 'really work': 1, 'Rating': 5, 'lik

{'i could': 1, 'a serious': 1, 'serious back': 1, 'wait my': 1, 'me from': 1, 'could not': 1, 'to purchasing': 1, 'item soooo': 1, 'thought of': 1, 'B000HVVSDU': 1, 'minute but': 1, 'my dentist': 1, 'stool is': 1, 'now i': 1, 'this item': 1, 'Verified': 0, 'of and': 1, 'problem recently': 1, 'inspiration i': 1, 'the kitchen': 1, 'purchased this': 1, 'my inspiration': 1, 'but now': 1, 'wa my': 1, 'stoolis adjustable': 1, 'honest </s>': 1, 'accessing microwave': 1, 'well a': 1, '<s> this': 1, 'the stoolis': 1, 'than minute': 1, 'soooo glad': 1, 'purchasing this': 1, 'cook top': 1, 'at various': 1, 'and purchased': 1, 'glad i': 1, 'prevents me': 1, 'can scoot': 1, 'top something': 1, 'wheelie but': 1, 'countertop the': 1, 'remain honest': 1, 'not do': 1, 'is a': 1, 'i can': 1, 'but wait': 1, 'for more': 1, 'standing for': 1, 'must remain': 1, 'microwave countertop': 1, 'dentist wa': 1, 'a cook': 1, 'height accessing': 1, 'incurred prevents': 1, 'adjustable a': 1, 'more than': 1, 'around t

KeyboardInterrupt: 